In [18]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
from scipy import stats
from ast import literal_eval
from sklearn.feature_extraction.text import TfidfVectorizer, CountVectorizer
from sklearn.metrics.pairwise import linear_kernel, cosine_similarity
from nltk.stem.snowball import SnowballStemmer
from nltk.stem.wordnet import WordNetLemmatizer
from nltk.corpus import wordnet
#from surprise import Reader, Dataset, SVD
import warnings; warnings.simplefilter('ignore')

In [19]:
from langdetect import detect, LangDetectException

In [20]:
# read the movies metadata dataset
md = pd. read_csv('C:/Users/rezzt/Desktop/DMQL project/Movies/movies_metadata.csv')
# display the first five row
md.head()

adult                              belongs_to_collection    budget   
0  False  {'id': 10194, 'name': 'Toy Story Collection', ...  30000000  \
1  False                                                NaN  65000000   
2  False  {'id': 119050, 'name': 'Grumpy Old Men Collect...         0   
3  False                                                NaN  16000000   
4  False  {'id': 96871, 'name': 'Father of the Bride Col...         0   

                                              genres   
0  [{'id': 16, 'name': 'Animation'}, {'id': 35, '...  \
1  [{'id': 12, 'name': 'Adventure'}, {'id': 14, '...   
2  [{'id': 10749, 'name': 'Romance'}, {'id': 35, ...   
3  [{'id': 35, 'name': 'Comedy'}, {'id': 18, 'nam...   
4                     [{'id': 35, 'name': 'Comedy'}]   

                               homepage     id    imdb_id original_language   
0  http://toystory.disney.com/toy-story    862  tt0114709                en  \
1                                   NaN   8844  tt0113497                en   
2                                   NaN  15602  tt0113228                en   
3                                   NaN  31357  tt0114885                en   
4                                   NaN  11862  tt0113041                en   

                original_title   
0                    Toy Story  \
1                      Jumanji   
2             Grumpier Old Men   
3            Waiting to Exhale   
4  Father of the Bride Part II   

                                            overview  ... release_date   
0  Led by Woody, Andy's toys live happily in his ...  ...   1995-10-30  \
1  When siblings Judy and Peter discover an encha...  ...   1995-12-15   
2  A family wedding reignites the ancient feud be...  ...   1995-12-22   
3  Cheated on, mistreated and stepped on, the wom...  ...   1995-12-22   
4  Just when George Banks has recovered from his ...  ...   1995-02-10   

       revenue runtime                                   spoken_languages   
0  373554033.0    81.0           [{'iso_639_1': 'en', 'name': 'English'}]  \
1  262797249.0   104.0  [{'iso_639_1': 'en', 'name': 'English'}, {'iso...   
2          0.0   101.0           [{'iso_639_1': 'en', 'name': 'English'}]   
3   81452156.0   127.0           [{'iso_639_1': 'en', 'name': 'English'}]   
4   76578911.0   106.0           [{'iso_639_1': 'en', 'name': 'English'}]   

     status                                            tagline   
0  Released                                                NaN  \
1  Released          Roll the dice and unleash the excitement!   
2  Released  Still Yelling. Still Fighting. Still Ready for...   
3  Released  Friends are the people who let you be yourself...   
4  Released  Just When His World Is Back To Normal... He's ...   

                         title  video vote_average vote_count  
0                    Toy Story  False          7.7     5415.0  
1                      Jumanji  False          6.9     2413.0  
2             Grumpier Old Men  False          6.5       92.0  
3            Waiting to Exhale  False          6.1       34.0  
4  Father of the Bride Part II  False          5.7      173.0  

[5 rows x 24 columns]

In [21]:
md.drop(['homepage'], axis=1, inplace=True)
genres = md['genres']
md.drop(['genres'], axis = 1, inplace=True)
genrelist=list(genres)
import ast
genre_names = [ [d['name'] for d in ast.literal_eval(genre_str)] for genre_str in genrelist ]
name = md['original_title']
nameDF = pd.DataFrame(name)
movie_id = md['id']
imdb_id = md['imdb_id']
nameDF['movie_id'] = movie_id
nameDF['imdb_id'] = imdb_id
nameDF['genres']=genre_names
nameDF['genres'] = nameDF['genres'].apply(lambda x: ', '.join(x))
nameDF = nameDF.replace('', np.nan)
release_date = md['release_date']
vote_average = md['vote_average']
nameDF['release_date'] = release_date
nameDF['vote_average'] = vote_average
nameDF

original_title movie_id    imdb_id   
0                        Toy Story      862  tt0114709  \
1                          Jumanji     8844  tt0113497   
2                 Grumpier Old Men    15602  tt0113228   
3                Waiting to Exhale    31357  tt0114885   
4      Father of the Bride Part II    11862  tt0113041   
...                            ...      ...        ...   
45461                      رگ خواب   439050  tt6209470   
45462          Siglo ng Pagluluwal   111109  tt2028550   
45463                     Betrayal    67758  tt0303758   
45464          Satana likuyushchiy   227506  tt0008536   
45465                     Queerama   461257  tt6980792   

                           genres release_date  vote_average  
0       Animation, Comedy, Family   1995-10-30           7.7  
1      Adventure, Fantasy, Family   1995-12-15           6.9  
2                 Romance, Comedy   1995-12-22           6.5  
3          Comedy, Drama, Romance   1995-12-22           6.1  
4                          Comedy   1995-02-10           5.7  
...                           ...          ...           ...  
45461               Drama, Family          NaN           4.0  
45462                       Drama   2011-11-17           9.0  
45463     Action, Drama, Thriller   2003-08-01           3.8  
45464                         NaN   1917-10-21           0.0  
45465                         NaN   2017-06-09           0.0  

[45466 rows x 6 columns]

In [22]:
budget = md['budget']
boxoffice = md['revenue']
prodcomp = md['production_companies']


In [23]:
import ast
prodlist = list(prodcomp)
prodnames = []
for prod_str in prodlist:
    try:
        # Attempt to parse the string to a Python object
        parsed = ast.literal_eval(prod_str)
        # Ensure that parsed is a list before attempting to iterate
        if isinstance(parsed, list):
            # Extract 'name' from each dictionary in the parsed list
            names = [d['name'] for d in parsed if 'name' in d]
            prodnames.append(names)
        else:
            # If parsed is not a list, append an empty list or handle accordingly
            prodnames.append([])
    except (ValueError, SyntaxError):
        # Handle malformed strings or 'nan' values by appending an empty list
        prodnames.append([])




In [24]:
production_distinct = []
for item in prodnames:
    for second in item:
        if second not in production_distinct:
            production_distinct.append(second)


In [25]:

prodid = []
for prod_str in prodlist:
    try:
        # Attempt to parse the string to a Python object
        parsed = ast.literal_eval(prod_str)
        # Ensure that parsed is a list before attempting to iterate
        if isinstance(parsed, list):
            # Extract 'name' from each dictionary in the parsed list
            id = [d['id'] for d in parsed if 'id' in d]
            prodid.append(id)
        else:
            # If parsed is not a list, append an empty list or handle accordingly
            prodid.append([])
    except (ValueError, SyntaxError):
        # Handle malformed strings or 'nan' values by appending an empty list
        prodid.append([])

In [26]:

name_id_mapping = {}
for names, ids in zip(prodnames, prodid):

    for name, id_ in zip(names, ids):

        name_id_mapping[name] = id_

name_id_mapping


{'Pixar Animation Studios': 3,
 'TriStar Pictures': 559,
 'Teitler Film': 2550,
 'Interscope Communications': 10201,
 'Warner Bros.': 6194,
 'Lancaster Gate': 19464,
 'Twentieth Century Fox Film Corporation': 306,
 'Sandollar Productions': 5842,
 'Touchstone Pictures': 9195,
 'Regency Enterprises': 508,
 'Forward Pass': 675,
 'Paramount Pictures': 4,
 'Scott Rudin Productions': 258,
 'Mirage Enterprises': 932,
 'Constellation Entertainment': 14941,
 'Worldwide': 55873,
 'Mont Blanc Entertainment GmbH': 58079,
 'Walt Disney Pictures': 2,
 'Universal Pictures': 33,
 'Imperial Entertainment': 21437,
 'Signature Entertainment': 23770,
 'United Artists': 60,
 'Eon Productions': 7576,
 'Columbia Pictures': 5,
 'Castle Rock Entertainment': 97,
 'Enigma Pictures': 6368,
 'Amblin Entertainment': 56,
 'Amblimation': 4105,
 'Hollywood Pictures': 915,
 'Cinergi Pictures Entertainment': 1504,
 'Le Studio Canal+': 183,
 'Laurence Mark Productions': 415,
 'Metro-Goldwyn-Mayer (MGM)': 8411,
 'Carolco 

In [27]:
credits = pd. read_csv('C:/Users/rezzt/Desktop/DMQL project/Movies/credits.csv')

In [28]:
credits.head()
I have a table that has the columns 'keywords' and 'keyword_id', that contains unique keywords and its ids. I want to map it into a larger movies table that returns movies that have these respective keywords. Give me explanations and python code for the same

cast   
0  [{'cast_id': 14, 'character': 'Woody (voice)',...  \
1  [{'cast_id': 1, 'character': 'Alan Parrish', '...   
2  [{'cast_id': 2, 'character': 'Max Goldman', 'c...   
3  [{'cast_id': 1, 'character': "Savannah 'Vannah...   
4  [{'cast_id': 1, 'character': 'George Banks', '...   

                                                crew     id  
0  [{'credit_id': '52fe4284c3a36847f8024f49', 'de...    862  
1  [{'credit_id': '52fe44bfc3a36847f80a7cd1', 'de...   8844  
2  [{'credit_id': '52fe466a9251416c75077a89', 'de...  15602  
3  [{'credit_id': '52fe44779251416c91011acb', 'de...  31357  
4  [{'credit_id': '52fe44959251416c75039ed7', 'de...  11862

In [29]:
cast = credits['cast']


In [30]:
cast = list(cast)

In [31]:
Productioncompanies = pd.DataFrame(list(name_id_mapping.items()), columns=['Production Company', 'Company ID'])


In [32]:
csv_file_path = 'C:/Users/rezzt/Desktop/DMQL project/Tables/production_companies.csv'  # Specify the path where you want to save the CSV file
Productioncompanies.to_csv(csv_file_path, index=False)

In [33]:
castname = list(cast)
cnames = []
for prod_str in castname:
    try:
        # Attempt to parse the string to a Python object
        parsed = ast.literal_eval(prod_str)
        # Ensure that parsed is a list before attempting to iterate
        if isinstance(parsed, list):
            # Extract 'name' from each dictionary in the parsed list
            names = [d['name'] for d in parsed if 'name' in d]
            cnames.append(names)
        else:
            # If parsed is not a list, append an empty list or handle accordingly
            cnames.append([])
    except (ValueError, SyntaxError):
        # Handle malformed strings or 'nan' values by appending an empty list
        cnames.append([])
cnames


[['Tom Hanks',
  'Tim Allen',
  'Don Rickles',
  'Jim Varney',
  'Wallace Shawn',
  'John Ratzenberger',
  'Annie Potts',
  'John Morris',
  'Erik von Detten',
  'Laurie Metcalf',
  'R. Lee Ermey',
  'Sarah Freeman',
  'Penn Jillette'],
 ['Robin Williams',
  'Jonathan Hyde',
  'Kirsten Dunst',
  'Bradley Pierce',
  'Bonnie Hunt',
  'Bebe Neuwirth',
  'David Alan Grier',
  'Patricia Clarkson',
  'Adam Hann-Byrd',
  'Laura Bell Bundy',
  'James Handy',
  'Gillian Barber',
  'Brandon Obray',
  'Cyrus Thiedeke',
  'Gary Joseph Thorup',
  'Leonard Zola',
  'Lloyd Berry',
  'Malcolm Stewart',
  'Annabel Kershaw',
  'Darryl Henriques',
  'Robyn Driscoll',
  'Peter Bryant',
  'Sarah Gilson',
  'Florica Vlad',
  'June Lion',
  'Brenda Lockmuller'],
 ['Walter Matthau',
  'Jack Lemmon',
  'Ann-Margret',
  'Sophia Loren',
  'Daryl Hannah',
  'Burgess Meredith',
  'Kevin Pollak'],
 ['Whitney Houston',
  'Angela Bassett',
  'Loretta Devine',
  'Lela Rochon',
  'Gregory Hines',
  'Dennis Haysbert',
 

In [34]:
cid = []
for prod_str in castname:
    try:
        # Attempt to parse the string to a Python object
        parsed = ast.literal_eval(prod_str)
        # Ensure that parsed is a list before attempting to iterate
        if isinstance(parsed, list):
            # Extract 'name' from each dictionary in the parsed list
            names = [d['id'] for d in parsed if 'id' in d]
            cid.append(names)
        else:
            # If parsed is not a list, append an empty list or handle accordingly
            cid.append([])
    except (ValueError, SyntaxError):
        # Handle malformed strings or 'nan' values by appending an empty list
        cid.append([])
cid

[[31,
  12898,
  7167,
  12899,
  12900,
  7907,
  8873,
  1116442,
  12901,
  12133,
  8655,
  12903,
  37221],
 [2157,
  8537,
  205,
  145151,
  5149,
  10739,
  58563,
  1276,
  46530,
  56523,
  51551,
  56522,
  1000304,
  188949,
  1076551,
  1480246,
  25024,
  27110,
  53715,
  1379424,
  1235504,
  25389,
  1483449,
  1483450,
  1483451,
  1483452],
 [6837, 3151, 13567, 16757, 589, 16523, 7166],
 [8851, 9780, 18284, 51359, 66804, 352, 87118, 34, 1276777, 10814],
 [67773,
  3092,
  519,
  70696,
  59222,
  18793,
  14592,
  20906,
  54348,
  209,
  26510,
  24358],
 [1158,
  380,
  5576,
  10127,
  3197,
  6200,
  15851,
  15852,
  34,
  524,
  15854,
  119232,
  31004,
  5587,
  15853,
  352,
  11160,
  9290,
  886,
  34839,
  4158,
  86602,
  158452,
  12799,
  3982,
  181343,
  81687,
  91756,
  160970,
  175600,
  12879,
  9258,
  167501,
  95145,
  58535,
  161939,
  6580,
  95796,
  166543,
  43010,
  37252,
  1457709,
  4971,
  941147,
  17358,
  4790,
  1090464,
  1090

In [35]:
actor_id_mapping = {}
for names, ids in zip(cnames, cid):
    # Update the dictionary with the new mappings
    actor_id_mapping.update({name: id_ for name, id_ in zip(names, ids)})


In [36]:
Actorslist = pd.DataFrame(list(actor_id_mapping.items()), columns=['Actor Name', 'Actor ID'])
Actorslist


Actor Name  Actor ID
0               Tom Hanks        31
1               Tim Allen     12898
2             Don Rickles      7167
3              Jim Varney     12899
4           Wallace Shawn     12900
...                   ...       ...
202742    Jeremy Lelliott    169498
202743      Jason Widener   1177500
202744     Kiko Ellsworth     93930
202745   Darrell Dubovsky   1686379
202746  Aleksandr Chabrov   1261758

[202747 rows x 2 columns]

In [37]:
csv_file_path = 'C:/Users/rezzt/Desktop/DMQL project/Tables/actors_list.csv'  # Specify the path where you want to save the CSV file
Actorslist.to_csv(csv_file_path, index=False)

In [38]:
cast = cnames

In [39]:
def safe_subtract(a, b):
    try:
        # Attempt to convert both to floats and subtract if possible
        return float(b) - float(a)
    except ValueError:
        # Return None or some other value indicating the operation couldn't be performed
        return None

# Subtract elements in boxoffice from their respective pairs in budget, skipping over errors
diff = [safe_subtract(a, b) for a, b in zip(budget, boxoffice)]






In [40]:
box_office_outcome = []

for count in range(len(diff)):
    try:
        # Skip the iteration if either value is None
        if diff[count] is None or budget[count] is None:
            continue
        
        # Attempt to convert both diff[count] and budget[count] to floats
        diff_value = float(diff[count])
        budget_value = float(budget[count])
        
        # Perform the comparison using the converted values
        if diff_value > (budget_value + (0.4 * budget_value)):
            box_office_outcome.append('Success')
        else:
            box_office_outcome.append('Failure')
    except (ValueError, TypeError):
        # Handle cases where conversion to float fails or input is None
        continue  # This will simply skip the current iteration
print(box_office_outcome)


['Success', 'Success', 'Failure', 'Success', 'Success', 'Success', 'Failure', 'Failure', 'Failure', 'Success', 'Failure', 'Failure', 'Success', 'Failure', 'Failure', 'Failure', 'Success', 'Failure', 'Success', 'Failure', 'Success', 'Failure', 'Failure', 'Failure', 'Success', 'Failure', 'Failure', 'Failure', 'Failure', 'Failure', 'Success', 'Success', 'Failure', 'Success', 'Failure', 'Success', 'Failure', 'Failure', 'Failure', 'Success', 'Failure', 'Failure', 'Failure', 'Success', 'Failure', 'Failure', 'Success', 'Success', 'Failure', 'Success', 'Failure', 'Failure', 'Failure', 'Failure', 'Failure', 'Failure', 'Success', 'Failure', 'Failure', 'Failure', 'Failure', 'Success', 'Failure', 'Failure', 'Failure', 'Success', 'Failure', 'Failure', 'Success', 'Failure', 'Failure', 'Success', 'Failure', 'Success', 'Failure', 'Failure', 'Failure', 'Failure', 'Failure', 'Failure', 'Failure', 'Failure', 'Failure', 'Failure', 'Failure', 'Failure', 'Failure', 'Success', 'Failure', 'Failure', 'Failure'

In [41]:
from itertools import zip_longest
import math  # For math.nan


# Using zip_longest to iterate through each element, replacing missing values with NaN
table = {}
try:
    for key, value1, value2, value3 in zip_longest(movie_id, budget, boxoffice, box_office_outcome, fillvalue=math.nan):
        table[key] = [value1, value2, value3]
except Exception as e:
    # Handle other exceptions if necessary
    print(f"An error occurred: {e}")

# The result_dict will have keys from 'keys' list and values as lists of corresponding elements from list1, list2, and list3.
# Missing values are filled with NaN.
print(table)


{'862': ['30000000', 373554033.0, 'Success'], '8844': ['65000000', 262797249.0, 'Success'], '15602': ['0', 0.0, 'Failure'], '31357': ['16000000', 81452156.0, 'Success'], '11862': ['0', 76578911.0, 'Success'], '949': ['60000000', 187436818.0, 'Success'], '11860': ['58000000', 0.0, 'Failure'], '45325': ['0', 0.0, 'Failure'], '9091': ['35000000', 64350171.0, 'Failure'], '710': ['58000000', 352194034.0, 'Success'], '9087': ['62000000', 107879496.0, 'Failure'], '12110': ['0', 0.0, 'Failure'], '21032': ['0', 11348324.0, 'Success'], '10858': ['44000000', 13681765.0, 'Failure'], '1408': ['98000000', 10017322.0, 'Failure'], '524': ['52000000', 116112375.0, 'Failure'], '4584': ['16500000', 135000000.0, 'Success'], '5': ['4000000', 4300000.0, 'Failure'], '9273': ['30000000', 212385533.0, 'Success'], '11517': ['60000000', 35431113.0, 'Failure'], '8012': ['30250000', 115101622.0, 'Success'], '1710': ['0', 0.0, 'Failure'], '9691': ['50000000', 30303072.0, 'Failure'], '12665': ['0', 0.0, 'Failure'], 

In [42]:
list_of_lists = [[key] + value for key, value in table.items()]
print(list_of_lists)

[['862', '30000000', 373554033.0, 'Success'], ['8844', '65000000', 262797249.0, 'Success'], ['15602', '0', 0.0, 'Failure'], ['31357', '16000000', 81452156.0, 'Success'], ['11862', '0', 76578911.0, 'Success'], ['949', '60000000', 187436818.0, 'Success'], ['11860', '58000000', 0.0, 'Failure'], ['45325', '0', 0.0, 'Failure'], ['9091', '35000000', 64350171.0, 'Failure'], ['710', '58000000', 352194034.0, 'Success'], ['9087', '62000000', 107879496.0, 'Failure'], ['12110', '0', 0.0, 'Failure'], ['21032', '0', 11348324.0, 'Success'], ['10858', '44000000', 13681765.0, 'Failure'], ['1408', '98000000', 10017322.0, 'Failure'], ['524', '52000000', 116112375.0, 'Failure'], ['4584', '16500000', 135000000.0, 'Success'], ['5', '4000000', 4300000.0, 'Failure'], ['9273', '30000000', 212385533.0, 'Success'], ['11517', '60000000', 35431113.0, 'Failure'], ['8012', '30250000', 115101622.0, 'Success'], ['1710', '0', 0.0, 'Failure'], ['9691', '50000000', 30303072.0, 'Failure'], ['12665', '0', 0.0, 'Failure'], 

In [43]:
box_office = pd.DataFrame(list_of_lists, columns=['movie_id', 'budget', 'box_office', 'outcome'])
print(box_office)

      movie_id    budget   box_office  outcome
0          862  30000000  373554033.0  Success
1         8844  65000000  262797249.0  Success
2        15602         0          0.0  Failure
3        31357  16000000   81452156.0  Success
4        11862         0   76578911.0  Success
...        ...       ...          ...      ...
45431   439050         0          0.0  Failure
45432   111109         0          0.0  Failure
45433    67758         0          0.0      NaN
45434   227506         0          0.0      NaN
45435   461257         0          0.0      NaN

[45436 rows x 4 columns]


In [44]:
csv_file_path = 'C:/Users/rezzt/Desktop/DMQL project/Tables/box_office.csv'  # Specify the path where you want to save the CSV file
box_office.to_csv(csv_file_path, index=False)

In [45]:
credits

cast   
0      [{'cast_id': 14, 'character': 'Woody (voice)',...  \
1      [{'cast_id': 1, 'character': 'Alan Parrish', '...   
2      [{'cast_id': 2, 'character': 'Max Goldman', 'c...   
3      [{'cast_id': 1, 'character': "Savannah 'Vannah...   
4      [{'cast_id': 1, 'character': 'George Banks', '...   
...                                                  ...   
45471  [{'cast_id': 0, 'character': '', 'credit_id': ...   
45472  [{'cast_id': 1002, 'character': 'Sister Angela...   
45473  [{'cast_id': 6, 'character': 'Emily Shaw', 'cr...   
45474  [{'cast_id': 2, 'character': '', 'credit_id': ...   
45475                                                 []   

                                                    crew      id  
0      [{'credit_id': '52fe4284c3a36847f8024f49', 'de...     862  
1      [{'credit_id': '52fe44bfc3a36847f80a7cd1', 'de...    8844  
2      [{'credit_id': '52fe466a9251416c75077a89', 'de...   15602  
3      [{'credit_id': '52fe44779251416c91011acb', 'de...   31357  
4      [{'credit_id': '52fe44959251416c75039ed7', 'de...   11862  
...                                                  ...     ...  
45471  [{'credit_id': '5894a97d925141426c00818c', 'de...  439050  
45472  [{'credit_id': '52fe4af1c3a36847f81e9b15', 'de...  111109  
45473  [{'credit_id': '52fe4776c3a368484e0c8387', 'de...   67758  
45474  [{'credit_id': '533bccebc3a36844cf0011a7', 'de...  227506  
45475  [{'credit_id': '593e676c92514105b702e68e', 'de...  461257  

[45476 rows x 3 columns]

In [46]:
castid = []
for prod_str in castname:
    try:
        # Attempt to parse the string to a Python object
        parsed = ast.literal_eval(prod_str)
        # Ensure that parsed is a list before attempting to iterate
        if isinstance(parsed, list):
            # Extract 'name' from each dictionary in the parsed list
            names = [d['cast_id'] for d in parsed if 'cast_id' in d]
            castid.append(names)
        else:
            # If parsed is not a list, append an empty list or handle accordingly
            castid.append([])
    except (ValueError, SyntaxError):
        # Handle malformed strings or 'nan' values by appending an empty list
        castid.append([])
castid

[[14, 15, 16, 17, 18, 19, 20, 26, 22, 23, 24, 25, 27],
 [1,
  8,
  2,
  24,
  10,
  25,
  26,
  11,
  14,
  13,
  31,
  12,
  28,
  29,
  30,
  32,
  33,
  34,
  35,
  36,
  37,
  50,
  39,
  40,
  41,
  42],
 [2, 3, 4, 5, 6, 9, 10],
 [1, 2, 3, 4, 5, 6, 8, 10, 20, 21],
 [1, 2, 3, 4, 13, 14, 15, 16, 17, 18, 19, 20],
 [25,
  26,
  27,
  28,
  29,
  30,
  31,
  32,
  33,
  38,
  35,
  39,
  41,
  42,
  34,
  36,
  46,
  47,
  37,
  43,
  44,
  48,
  50,
  54,
  55,
  51,
  56,
  52,
  53,
  59,
  60,
  96,
  97,
  99,
  100,
  101,
  102,
  104,
  109,
  110,
  112,
  116,
  115,
  123,
  45,
  49,
  57,
  58,
  94,
  95,
  98,
  103,
  105,
  106,
  107,
  111,
  113,
  114,
  118,
  119,
  120,
  121,
  122,
  124,
  133],
 [1,
  2,
  3,
  4,
  11,
  12,
  13,
  14,
  15,
  16,
  17,
  56,
  57,
  58,
  59,
  60,
  61,
  62,
  63,
  64,
  65,
  66,
  67,
  68,
  69,
  70,
  71,
  72,
  73,
  74,
  75,
  76,
  77,
  78,
  79,
  80,
  81,
  82,
  83,
  84,
  85,
  86,
  87,
  88,
  89,
  

In [47]:
crew = credits['crew']
crewname = list(crew)
directornames = []
writernames = []
cinematographer = []
for prod_str in crewname:
    try:
        # Attempt to parse the string to a Python object
        parsed = ast.literal_eval(prod_str)
        # Ensure that parsed is a list before attempting to iterate
        if isinstance(parsed, list):
            # Extract 'name' from each dictionary in the parsed list
            names = [d['name'] for d in parsed if 'name' in d]
            cnames.append(names)
        else:
            # If parsed is not a list, append an empty list or handle accordingly
            cnames.append([])
    except (ValueError, SyntaxError):
        # Handle malformed strings or 'nan' values by appending an empty list
        cnames.append([])
cnames


KeyboardInterrupt: 

In [48]:
cast_withid = list(zip(movie_id, cnames))
cast_withid

[('862',
  ['Tom Hanks',
   'Tim Allen',
   'Don Rickles',
   'Jim Varney',
   'Wallace Shawn',
   'John Ratzenberger',
   'Annie Potts',
   'John Morris',
   'Erik von Detten',
   'Laurie Metcalf',
   'R. Lee Ermey',
   'Sarah Freeman',
   'Penn Jillette']),
 ('8844',
  ['Robin Williams',
   'Jonathan Hyde',
   'Kirsten Dunst',
   'Bradley Pierce',
   'Bonnie Hunt',
   'Bebe Neuwirth',
   'David Alan Grier',
   'Patricia Clarkson',
   'Adam Hann-Byrd',
   'Laura Bell Bundy',
   'James Handy',
   'Gillian Barber',
   'Brandon Obray',
   'Cyrus Thiedeke',
   'Gary Joseph Thorup',
   'Leonard Zola',
   'Lloyd Berry',
   'Malcolm Stewart',
   'Annabel Kershaw',
   'Darryl Henriques',
   'Robyn Driscoll',
   'Peter Bryant',
   'Sarah Gilson',
   'Florica Vlad',
   'June Lion',
   'Brenda Lockmuller']),
 ('15602',
  ['Walter Matthau',
   'Jack Lemmon',
   'Ann-Margret',
   'Sophia Loren',
   'Daryl Hannah',
   'Burgess Meredith',
   'Kevin Pollak']),
 ('31357',
  ['Whitney Houston',
   'Ang

In [49]:
Cast_table = pd.DataFrame(cast_withid, columns=['movie_id', 'cast'])
Cast_table['cast'] = Cast_table['cast'].apply(lambda x: ', '.join(x))

print(Cast_table)

      movie_id                                               cast
0          862  Tom Hanks, Tim Allen, Don Rickles, Jim Varney,...
1         8844  Robin Williams, Jonathan Hyde, Kirsten Dunst, ...
2        15602  Walter Matthau, Jack Lemmon, Ann-Margret, Soph...
3        31357  Whitney Houston, Angela Bassett, Loretta Devin...
4        11862  Steve Martin, Diane Keaton, Martin Short, Kimb...
...        ...                                                ...
45461   439050                      Jeanne d'Alcy, Georges Méliès
45462   111109                                                   
45463    67758  Sridevi Kapoor, Sajal Ali, Akshaye Khanna, Naw...
45464   227506  Markie Adams, Roberto Aguire, Tina Arning, Lau...
45465   461257  Giulio Brogi, Renato Cestiè, Vito Cipolla, Dan...

[45466 rows x 2 columns]


In [50]:
csv_file_path = 'C:/Users/rezzt/Desktop/DMQL project/Tables/cast_list.csv'  # Specify the path where you want to save the CSV file
Cast_table.to_csv(csv_file_path, index=False)

In [51]:
nameDF['ProductionID'] = prodid
nameDF

original_title movie_id    imdb_id   
0                        Toy Story      862  tt0114709  \
1                          Jumanji     8844  tt0113497   
2                 Grumpier Old Men    15602  tt0113228   
3                Waiting to Exhale    31357  tt0114885   
4      Father of the Bride Part II    11862  tt0113041   
...                            ...      ...        ...   
45461                      رگ خواب   439050  tt6209470   
45462          Siglo ng Pagluluwal   111109  tt2028550   
45463                     Betrayal    67758  tt0303758   
45464          Satana likuyushchiy   227506  tt0008536   
45465                     Queerama   461257  tt6980792   

                           genres release_date  vote_average   
0       Animation, Comedy, Family   1995-10-30           7.7  \
1      Adventure, Fantasy, Family   1995-12-15           6.9   
2                 Romance, Comedy   1995-12-22           6.5   
3          Comedy, Drama, Romance   1995-12-22           6.1   
4                          Comedy   1995-02-10           5.7   
...                           ...          ...           ...   
45461               Drama, Family          NaN           4.0   
45462                       Drama   2011-11-17           9.0   
45463     Action, Drama, Thriller   2003-08-01           3.8   
45464                         NaN   1917-10-21           0.0   
45465                         NaN   2017-06-09           0.0   

             ProductionID  
0                     [3]  
1      [559, 2550, 10201]  
2           [6194, 19464]  
3                   [306]  
4            [5842, 9195]  
...                   ...  
45461                  []  
45462             [19653]  
45463              [6165]  
45464             [88753]  
45465                  []  

[45466 rows x 7 columns]

In [52]:
mapped_list = list(zip(movie_id, prodid))



In [53]:
expanded_mapping = [(movie_id, prod_id) for movie_id, prod_ids in mapped_list for prod_id in prod_ids]

expanded_mapping

[('862', 3),
 ('8844', 559),
 ('8844', 2550),
 ('8844', 10201),
 ('15602', 6194),
 ('15602', 19464),
 ('31357', 306),
 ('11862', 5842),
 ('11862', 9195),
 ('949', 508),
 ('949', 675),
 ('949', 6194),
 ('11860', 4),
 ('11860', 258),
 ('11860', 932),
 ('11860', 5842),
 ('11860', 14941),
 ('11860', 55873),
 ('11860', 58079),
 ('45325', 2),
 ('9091', 33),
 ('9091', 21437),
 ('9091', 23770),
 ('710', 60),
 ('710', 7576),
 ('9087', 5),
 ('9087', 97),
 ('12110', 5),
 ('12110', 97),
 ('12110', 6368),
 ('21032', 33),
 ('21032', 56),
 ('21032', 4105),
 ('10858', 915),
 ('10858', 1504),
 ('1408', 183),
 ('1408', 415),
 ('1408', 8411),
 ('1408', 14723),
 ('524', 33),
 ('524', 10898),
 ('524', 11583),
 ('524', 11584),
 ('4584', 441),
 ('4584', 932),
 ('5', 14),
 ('5', 59),
 ('9273', 5682),
 ('9273', 6194),
 ('9273', 10210),
 ('11517', 5),
 ('8012', 216),
 ('8012', 8411),
 ('1710', 508),
 ('1710', 10104),
 ('9691', 1885),
 ('9691', 5358),
 ('9691', 6194),
 ('9691', 10308),
 ('9691', 23397),
 ('9691'

In [54]:
ProductionMap = pd.DataFrame(expanded_mapping, columns=['movie_id', 'Company_id'])

# Display the DataFrame
print(ProductionMap)

      movie_id  Company_id
0          862           3
1         8844         559
2         8844        2550
3         8844       10201
4        15602        6194
...        ...         ...
70540    30840       16323
70541    30840       38978
70542   111109       19653
70543    67758        6165
70544   227506       88753

[70545 rows x 2 columns]


In [ ]:
csv_file_path = 'C:/Users/rezzt/Desktop/DMQL project/Tables/production_map.csv'  # Specify the path where you want to save the CSV file
ProductionMap.to_csv(csv_file_path, index=False)

In [ ]:
nameDF.drop('ProductionID', axis=1, inplace=True)
nameDF


original_title movie_id    imdb_id   
0                        Toy Story      862  tt0114709  \
1                          Jumanji     8844  tt0113497   
2                 Grumpier Old Men    15602  tt0113228   
3                Waiting to Exhale    31357  tt0114885   
4      Father of the Bride Part II    11862  tt0113041   
...                            ...      ...        ...   
45461                      رگ خواب   439050  tt6209470   
45462          Siglo ng Pagluluwal   111109  tt2028550   
45463                     Betrayal    67758  tt0303758   
45464          Satana likuyushchiy   227506  tt0008536   
45465                     Queerama   461257  tt6980792   

                           genres release_date  vote_average  
0       Animation, Comedy, Family   1995-10-30           7.7  
1      Adventure, Fantasy, Family   1995-12-15           6.9  
2                 Romance, Comedy   1995-12-22           6.5  
3          Comedy, Drama, Romance   1995-12-22           6.1  
4                          Comedy   1995-02-10           5.7  
...                           ...          ...           ...  
45461               Drama, Family          NaN           4.0  
45462                       Drama   2011-11-17           9.0  
45463     Action, Drama, Thriller   2003-08-01           3.8  
45464                         NaN   1917-10-21           0.0  
45465                         NaN   2017-06-09           0.0  

[45466 rows x 6 columns]

In [ ]:
nameDF.drop('imdb_id', axis=1, inplace=True)

In [ ]:
keyworddata = pd. read_csv('C:/Users/rezzt/Desktop/DMQL project/Movies/keywords.csv')
keyworddata.head()

id                                           keywords
0    862  [{'id': 931, 'name': 'jealousy'}, {'id': 4290,...
1   8844  [{'id': 10090, 'name': 'board game'}, {'id': 1...
2  15602  [{'id': 1495, 'name': 'fishing'}, {'id': 12392...
3  31357  [{'id': 818, 'name': 'based on novel'}, {'id':...
4  11862  [{'id': 1009, 'name': 'baby'}, {'id': 1599, 'n...

In [ ]:
k = list(keyworddata['keywords'])
k

In [ ]:
keyid = []
keyname = []

for item in k:
    # Convert the string representation of a list into an actual list
    item_list = ast.literal_eval(item)
    # Extract and append 'id' and 'name' to their respective lists
    for d in item_list:
        keyid.append(d['id'])
        keyname.append(d['name'])

In [ ]:
mappedkeywords = list(zip(keyid, keyname))
mappedkeywords

In [ ]:
Keywords = pd.DataFrame(mappedkeywords, columns=['key_id', 'keyword'])
Keywords

key_id       keyword
0          931      jealousy
1         4290           toy
2         5202           boy
3         6054    friendship
4         9713       friends
...        ...           ...
158675   11800  mockumentary
158676   10703   tragic love
158677    2679        artist
158678   14531          play
158679  215397         pinoy

[158680 rows x 2 columns]

In [ ]:
csv_file_path = 'C:/Users/rezzt/Desktop/DMQL project/Tables/keyword_list.csv'  # Specify the path where you want to save the CSV file
Keywords.to_csv(csv_file_path, index=False)

In [ ]:
keyworddata['keywords'] = keyworddata['keywords'].apply(ast.literal_eval)

# Extracting tuples of movie id and corresponding list of keyword ids
result = [(row['id'], [keyword['id'] for keyword in row['keywords']]) for index, row in keyworddata.iterrows()]

# The result variable contains the list of tuples as requested
print(result)

[(862, [931, 4290, 5202, 6054, 9713, 9823, 165503, 170722, 187065]), (8844, [10090, 10941, 15101, 33467, 158086, 158091]), (15602, [1495, 12392, 179431, 208510]), (31357, [818, 10131, 14768, 15160, 33455]), (11862, [1009, 1599, 2246, 4995, 5600, 10707, 13149, 33358, 170521]), (949, [642, 703, 974, 1523, 3713, 7281, 9727, 9812, 9826, 9937, 10051, 10085, 10594, 10726, 15076, 18023, 34117, 156121, 159343, 159434, 167104, 192261, 207268, 208009, 214983]), (11860, [90, 380, 2072, 9398, 9492, 33626]), (45325, []), (9091, [949, 1562, 1653, 193533]), (710, [701, 769, 1308, 2812, 3268, 3272, 3278, 3376, 3531, 3560, 3561, 3562, 3563, 3564, 193008]), (9087, [833, 840, 1605, 33476, 211505]), (12110, [3633, 11931]), (21032, [1994, 6411, 9880, 15162, 15169, 158175, 158370, 158371]), (10858, [840, 2946, 4240, 5565, 6086, 6165]), (1408, [911, 1454, 1969, 3799, 5470, 12988]), (524, [383, 726, 1228, 2635, 33625]), (4584, [420, 818, 964, 2755, 7564, 10911, 11109, 15060, 156507, 156510, 156512]), (5, [612

In [ ]:
mapped_data = [(movie_id, keyword_id) for movie_id, keyword_list in result for keyword_id in keyword_list]


In [ ]:
Keywordmap = pd.DataFrame(mapped_data, columns=['movie_id', 'keyword_id'])

# Display the DataFrame
print(Keywordmap)

In [ ]:
csv_file_path = 'C:/Users/rezzt/Desktop/DMQL project/Tables/keyword_map.csv'  # Specify the path where you want to save the CSV file
Keywordmap.to_csv(csv_file_path, index=False)

In [ ]:
csv_file_path = 'C:/Users/rezzt/Desktop/DMQL project/Tables/movies.csv'  # Specify the path where you want to save the CSV file
nameDF.to_csv(csv_file_path, index=False)

In [2]:

def is_english(text):
    try:
        return detect(text) == 'en'
    except LangDetectException:
        return False  # Assume non-English if detection fails

# Apply the function to each title in the original_title column
nameDF['is_english'] = nameDF['original_title'].apply(is_english)

# Filter the DataFrame to keep only English titles and drop the is_english column
df_filtered = nameDF[nameDF['is_english']].drop('is_english', axis=1)

print(df_filtered)

NameError: name 'nameDF' is not defined